In [1]:
# import the necessary packages
import numpy as np
import sys
import datetime
import time
import pandas as pd
import numpy as np
from sklearn import cross_validation
from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier, GradientBoostingClassifier
from sklearn.svm import LinearSVC, LinearSVR
from sklearn.linear_model import SGDClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import AdaBoostClassifier, GradientBoostingClassifier
from sklearn.metrics import accuracy_score, confusion_matrix
from sklearn.metrics import f1_score
from sklearn.utils import shuffle
# from nolearn.dbn import DBN
import timeit




/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/cross_validation.py:41: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)


In [2]:
def load_fold_list(fold_list_number):
    import glob
    list_path = '/Users/sam/Documents/USF/homework/cs686-02/HCI/lab/final_project/file-video-stream/SMILE_DATABASE/experimental_protocols/fold_all'
    #         list_path = list_directory_name
    allFiles = glob.glob(list_path + "/*.txt")
#     print(len(list_path))
    whole_fold_list = []
    train_fold_list = []
    test_fold_list = []
    i = 1
    
    while i < 11:
        
        file_ = list_path + "/fold_all_" + str(i) + ".txt"
    
#         print (file_)
        with open(file_) as f:
            content = f.readlines()
            content = [x.strip() for x in content]
            whole_fold_list.append(content)
        i+=1
        
        
    test_fold_list = whole_fold_list[fold_list_number]
    for x in whole_fold_list:
        if x != test_fold_list:
            train_fold_list.extend(x)
        
    return train_fold_list,test_fold_list

In [3]:
train_fold_list,test_fold_list = load_fold_list(1)
print(len(train_fold_list))
print(len(test_fold_list))

1114
126


In [43]:
def read_data(fold_list_number):
        import glob
        # deli_training_path = '/Users/sam/Documents/USF/homework/cs686-02/HCI/lab/final_project/file-video-stream/videos/deliberate/results'
        """
        if 'deliberate' in directory_name:
            label = 0
        else:
            label = 1
        """
        training_fold_list,test_fold_list = load_fold_list(fold_list_number)
        #  we need to load spontaneous and deliberate seperately
        deli_training_path = 'file-video-stream/videos/deliberate/aggregated_30_results/training_set/'
        deli_allFiles = glob.glob(deli_training_path + "/*.csv")
        deli_training_df = pd.DataFrame()
        deli_test_df = pd.DataFrame()
        deli_training_list_ = []
        deli_test_list_ = []
        
        for file_ in deli_allFiles:
            df = pd.read_csv(file_)
            
            label = 0
            file_name = file_[len(deli_training_path) :len(deli_training_path)+22]
            # print(file_name)
            if file_name in training_fold_list:
                deli_training_list_.append(df)
            else:
                deli_test_list_.append(df)

        deli_training_df = pd.concat(deli_training_list_)
        deli_test_df = pd.concat(deli_test_list_)
        deli_training_df['Label'] = 0
        deli_test_df['Label'] = 0
        
        spon_training_path = 'file-video-stream/videos/spontaneous/aggregated_30_results/training_set/'
        spon_allFiles = glob.glob(spon_training_path + "/*.csv")
        spon_training_df = pd.DataFrame()
        spon_test_df = pd.DataFrame()
        spon_training_list_ = []
        spon_test_list_ = []
        
        for file_ in spon_allFiles:
            df = pd.read_csv(file_)
            
            label = 0
            file_name = file_[len(spon_training_path) :len(spon_training_path)+23]
            if file_name in training_fold_list:
                spon_training_list_.append(df)
            else:
                spon_test_list_.append(df)

        spon_training_df = pd.concat(spon_training_list_)
        spon_test_df = pd.concat(spon_test_list_)
        spon_training_df['Label'] = 1
        spon_test_df['Label'] = 1
        
        traing_list = [spon_training_df, deli_training_df]
        traing_df = pd.concat(traing_list)
        
        test_list = [spon_test_df, deli_test_df]
        test_df = pd.concat(test_list)
        
        return traing_df, test_df

In [44]:
traing_df, test_df = read_data(0)

In [46]:
traing_df.head()
print(traing_df.count())

Unnamed: 0    6289
A             6289
B             6289
C             6289
D             6289
E             6289
F             6289
G             6289
H             6289
SD1           6289
SD2           6289
SD3           6289
SD4           6289
SD5           6289
SD6           6289
SD7           6289
SD8           6289
Label         6289
dtype: int64


In [47]:
print(test_df.count())

Unnamed: 0    786
A             786
B             786
C             786
D             786
E             786
F             786
G             786
H             786
SD1           786
SD2           786
SD3           786
SD4           786
SD5           786
SD6           786
SD7           786
SD8           786
Label         786
dtype: int64


In [60]:
# set input X values
shffule_traing_df = shuffle(traing_df)
shffule_test_df = shuffle(test_df)
features = traing_df.columns[1:17]
# print(features)
X_train = shffule_traing_df[features]
y_train = shffule_traing_df['Label']

X_test = shffule_test_df[features]
y_test = shffule_test_df['Label']


In [61]:
X_train.head()

A          B          C           D          E          F  \
4  12.129041  12.030420  24.471085   91.930729  82.529137  83.055847   
1  12.969823  11.738720  19.628446   96.216966  89.549083  87.430700   
5  14.021486  11.935622  15.974691  105.500640  85.349277  81.381577   
2  10.927834   9.695868  16.548617   85.095823  76.547588  76.180202   
3  13.290291  12.117897  15.717355   93.301828  84.722318  83.422452   

           G          H       SD1       SD2       SD3       SD4       SD5  \
4  13.418796  13.040230  0.535141  0.449796  1.048496  1.083710  1.573156   
1  13.265640  12.780412  0.342099  0.518760  0.625124  0.543602  0.601407   
5  13.666812  13.148298  0.362316  0.490850  0.492523  0.498343  0.658997   
2  11.289117  11.279827  0.386155  0.506759  0.493246  0.409461  0.547771   
3  13.523384  12.984769  0.448876  0.435771  0.656827  0.368140  0.749818   

        SD6       SD7       SD8  
4  0.927126  0.411398  0.534553  
1  0.522158  0.506093  0.307241  
5  0.488873  0.430024  0.394442  
2  0.526106  0.394757  0.406832  
3  0.511101  0.389114  0.249880

In [62]:
y_train.head()

4    1
1    0
5    1
2    1
3    1
Name: Label, dtype: int64

# Follow UvA-NEMO Protocol, Train on 9 folds, Test on 1 fold. 
## Specially for Hidden Markov Models (HMMs)

In [4]:
import hmmlearn.hmm as hmm

# we need to load data in a new way
# generate clip sequences firrstly
# we start from a new read data method
# we will return two training matrix, deli_training_matrix and spon_training_matrix, 
# and then use them to train two seperate hidden markov models, calculate and compare the likelihood.


In [5]:
def hmm_read_data(fold_list_number):
        import glob
        # deli_training_path = '/Users/sam/Documents/USF/homework/cs686-02/HCI/lab/final_project/file-video-stream/videos/deliberate/results'
        """
        if 'deliberate' in directory_name:
            label = 0
        else:
            label = 1
        """
        training_fold_list,test_fold_list = load_fold_list(fold_list_number)
        train_label_list = []
        test_label_list = []
        training_matrix = []
        test_matrix = []
        #  we need to load spontaneous and deliberate seperately
        deli_training_path = 'file-video-stream/videos/deliberate/aggregated_30_results/training_set/'
        deli_allFiles = glob.glob(deli_training_path + "/*.csv")
        # deli_training_df = pd.DataFrame()
        # deli_test_df = pd.DataFrame()
        deli_training_list_ = []
        deli_test_list_ = []
        deli_training_matrix = []
        deli_test_matrix = []
        
        for file_ in deli_allFiles:
            df = pd.read_csv(file_)
            
            label = 0
            file_name = file_[len(deli_training_path) :len(deli_training_path)+22]
            # print(file_name)
            
            df.drop(df.columns[0], axis=1, inplace=True)
            if file_name in training_fold_list:
                deli_training_list_.append(df.values.tolist())
                
                train_label_list.append(label)
            else:
                deli_test_list_.append(df.values.tolist())
                test_label_list.append(label)
            
        # this is a list of clip pandaframes, we should convet each one to a numpy sequence
#         print(len(deli_training_list_))
        # deli_training_df = pd.concat(deli_training_list_)
        # deli_test_df = pd.concat(deli_test_list_)
        # deli_training_df['Label'] = 0
        # deli_test_df['Label'] = 0
        
        spon_training_path = 'file-video-stream/videos/spontaneous/aggregated_30_results/training_set/'
        spon_allFiles = glob.glob(spon_training_path + "/*.csv")
        spon_training_df = pd.DataFrame()
        spon_test_df = pd.DataFrame()
        spon_training_list_ = []
        spon_test_list_ = []
        spon_training_matrix = []
        spon_test_matrix = []
        
        for file_ in spon_allFiles:
            df = pd.read_csv(file_)
            
            label = 1
            file_name = file_[len(spon_training_path) :len(spon_training_path)+23]
            df.drop(df.columns[0], axis=1, inplace=True)
            if file_name in training_fold_list:
                spon_training_list_.append(df.values.tolist())
                train_label_list.append(label)
            else:
                spon_test_list_.append(df.values.tolist())
                test_label_list.append(label)
        
        print(len(train_label_list))
        print(len(test_label_list))
        
        # temp_training_matrix = [deli_training_list_, spon_training_list_]
        training_matrix = np.concatenate([deli_training_list_, spon_training_list_])
        print (len(training_matrix))
        
        test_matrix = np.concatenate([deli_test_list_, spon_test_list_])
        print (len(test_matrix))
        # spon_training_df = pd.concat(spon_training_list_)
        # spon_test_df = pd.concat(spon_test_list_)
        # spon_training_df['Label'] = 1
        # spon_test_df['Label'] = 1
        
        
        # traing_list = [spon_training_df, deli_training_df]
        # traing_df = pd.concat(traing_list)
        
        # test_list = [spon_test_df, deli_test_df]
        # test_df = pd.concat(test_list)
        
        return deli_training_list_, spon_training_list_, training_matrix, test_matrix, train_label_list, test_label_list

In [6]:
deli_training_matrix, spon_training_matrix, training_matrix, test_matrix, train_label_list, test_label_list = hmm_read_data(1)



1052
121
1052
121


In [7]:
# firstly we use a deliberate training matrix to train a HMM
from hmmlearn import hmm
deli_lengths = []
i = 0
# print(len(deli_training_matrix))
while i < len(deli_training_matrix):
    # print(len(deli_training_matrix[i]))
    deli_lengths.append(len(deli_training_matrix[i]))
    i += 1

# print (deli_training_matrix[0])
# print(len(deli_lengths))   
new_deli_training_matrix = np.concatenate(deli_training_matrix)
deli_model = hmm.GaussianHMM(n_components=2, covariance_type="full", n_iter=100)
deli_model.fit(new_deli_training_matrix,deli_lengths)
score = deli_model.score(test_matrix[0])

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function distribute_covar_matrix_to_match_covariance_type is deprecated; The function distribute_covar_matrix_to_match_covariance_typeis deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(ms

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/

...

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/

In [8]:
print(np.exp(score))






4.89924567183e-17


In [9]:
# secondly we use a spontaneous training matrix to train a HMM
spon_lengths = []
i = 0
# print(len(spon_training_matrix))
while i < len(spon_training_matrix):
    # print(len(deli_training_matrix[i]))
    spon_lengths.append(len(spon_training_matrix[i]))
    i += 1

# print (spon_training_matrix[0])
# print(len(spon_lengths))   
new_spon_training_matrix = np.concatenate(spon_training_matrix)
spon_model = hmm.GaussianHMM(n_components=2, covariance_type="full", n_iter=100)
spon_model.fit(new_spon_training_matrix,spon_lengths)
score = spon_model.score(test_matrix[0])

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function distribute_covar_matrix_to_match_covariance_type is deprecated; The function distribute_covar_matrix_to_match_covariance_typeis deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(ms

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/

...

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/

In [11]:
# at last, we used these two trained HMMs to decode test matrix and compare the likelihood, generate results
# we compare test results, get accuracy
accuracy = 0
hmm_test_result_list = []
i = 0
j = 0
score = spon_model.score(test_matrix[0])

# compare np.exp(score)

while i < len(test_matrix):
    deli_score = np.exp(deli_model.score(test_matrix[i]))
    spon_score = np.exp(spon_model.score(test_matrix[i]))
    if deli_score >= spon_score:
        hmm_test_result_list.append(0)
    else:
        hmm_test_result_list.append(1)
    i += 1
        
while j < len(test_label_list):
    if hmm_test_result_list[j] == test_label_list[j]:
        accuracy +=1
    j +=1
        
accuracy = float(accuracy) / float(len(test_label_list))

print(accuracy)
    

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/

0.45454545454545453


/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/utils/deprecation.py:77: DeprecationWarning: Function log_multivariate_normal_density is deprecated; The function log_multivariate_normal_density is deprecated in 0.18 and will be removed in 0.20.
  warnings.warn(msg, category=DeprecationWarning)
/

In [12]:
print(accuracy)




0.45454545454545453


# Follow UvA-NEMO Protocol, Train on 9 folds, Test on 1 fold.

In [65]:
# running linear SVM model
# we will run it for ten times, then get
i = 0
average_acc = 0
average_fscore = 0
while i < 10:
    print (i)
    traing_df, test_df = read_data(i)
    shffule_traing_df = shuffle(traing_df)
    shffule_test_df = shuffle(test_df)
    features = traing_df.columns[1:17]
    # print(features)
    X_train = shffule_traing_df[features]
    y_train = shffule_traing_df['Label']

    X_test = shffule_test_df[features]
    y_test = shffule_test_df['Label']
    
    clf_svm = LinearSVC()
    clf_svm.fit(X_train, y_train)
    y_pred_svm = clf_svm.predict(X_test)
    acc_svm = accuracy_score(y_test, y_pred_svm)
    f_score = f1_score(y_test, y_pred_svm, average='weighted')
    average_acc += acc_svm
    average_fscore += f_score
    print ("Linear SVM accuracy: ",acc_svm)
    print ("Linear SVM F-score: ",f_score)
    print (confusion_matrix(y_test, y_pred_svm))
    
    con_matrix = []
    con_matrix = confusion_matrix(y_test, y_pred_svm)
    P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
    print ("Linear SVM accuracy of precision true: ",P_true)
    P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
    print ("Linear SVM accuracy of precision false: ",P_false)
    
    i += 1

average_acc = average_acc/10
average_fscore = average_fscore/10

print ("Average Linear SVM accuracy: ",average_acc)
print ("Average SVM F-score: ",average_fscore)



0


/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/ipykernel_launcher.py:32: RuntimeWarning: invalid value encountered in long_scalars


Linear SVM accuracy:  0.632315521628
Linear SVM F-score:  0.489884355806
[[  0 289]
 [  0 497]]
Linear SVM accuracy of precision true:  nan
Linear SVM accuracy of precision false:  0.632315521628
1
Linear SVM accuracy:  0.414634146341
Linear SVM F-score:  0.243061396131
[[306   0]
 [432   0]]
Linear SVM accuracy of precision true:  0.414634146341
Linear SVM accuracy of precision false:  nan
2


/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/ipykernel_launcher.py:34: RuntimeWarning: invalid value encountered in long_scalars


Linear SVM accuracy:  0.61744966443
Linear SVM F-score:  0.473463477123
[[  0 283]
 [  2 460]]
Linear SVM accuracy of precision true:  0.0
Linear SVM accuracy of precision false:  0.619111709287
3
Linear SVM accuracy:  0.603846153846
Linear SVM F-score:  0.454694705774
[[  0 309]
 [  0 471]]
Linear SVM accuracy of precision true:  nan
Linear SVM accuracy of precision false:  0.603846153846
4
Linear SVM accuracy:  0.604748603352
Linear SVM F-score:  0.455798338123
[[  0 283]
 [  0 433]]
Linear SVM accuracy of precision true:  nan
Linear SVM accuracy of precision false:  0.604748603352
5
Linear SVM accuracy:  0.584487534626
Linear SVM F-score:  0.43121283149
[[  0 300]
 [  0 422]]
Linear SVM accuracy of precision true:  nan
Linear SVM accuracy of precision false:  0.584487534626
6
Linear SVM accuracy:  0.632298136646
Linear SVM F-score:  0.489862635545
[[  0 296]
 [  0 509]]
Linear SVM accuracy of precision true:  nan
Linear SVM accuracy of precision false:  0.632298136646
7
Linear SVM a

In [82]:
# running random forest model
# we will run it for ten times, then get
i = 0
average_acc = 0
average_fscore = 0
while i < 10:
    print (i)
    traing_df, test_df = read_data(i)
    shffule_traing_df = shuffle(traing_df)
    shffule_test_df = shuffle(test_df)
    features = traing_df.columns[1:17]
    # print(features)
    X_train = shffule_traing_df[features]
    y_train = shffule_traing_df['Label']

    X_test = shffule_test_df[features]
    y_test = shffule_test_df['Label']
    
    clf_rf = RandomForestClassifier()
    clf_rf.fit(X_train, y_train)
    y_pred_rf = clf_rf.predict(X_test)
    acc_rf = accuracy_score(y_test, y_pred_rf)
    f_score = f1_score(y_test, y_pred_rf, average='weighted')
    average_acc += acc_rf
    average_fscore += f_score
    print ("random forest accuracy: ",acc_rf)
    print ("random forest F-score: ",f_score)
    print (confusion_matrix(y_test, y_pred_rf))

    con_matrix = []
    con_matrix = confusion_matrix(y_test, y_pred_rf)
    P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
    print ("random forest accuracy of precision true: ",P_true)
    P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
    print ("random forest accuracy of precision false: ",P_false)
    
    i += 1

average_acc = average_acc/10
average_fscore = average_fscore/10

print ("Average random forest accuracy: ",average_acc)
print ("Average random forest F-score: ",average_fscore)

0
random forest accuracy:  0.502544529262
random forest F-score:  0.50766829514
[[111 178]
 [213 284]]
random forest accuracy of precision true:  0.342592592593
random forest accuracy of precision false:  0.614718614719
1
random forest accuracy:  0.491869918699
random forest F-score:  0.494779369757
[[135 171]
 [204 228]]
random forest accuracy of precision true:  0.398230088496
random forest accuracy of precision false:  0.571428571429
2
random forest accuracy:  0.551677852349
random forest F-score:  0.557397551982
[[144 139]
 [195 267]]
random forest accuracy of precision true:  0.424778761062
random forest accuracy of precision false:  0.65763546798
3
random forest accuracy:  0.560256410256
random forest F-score:  0.560616127042
[[139 170]
 [173 298]]
random forest accuracy of precision true:  0.445512820513
random forest accuracy of precision false:  0.636752136752
4
random forest accuracy:  0.526536312849
random forest F-score:  0.531101697583
[[137 146]
 [193 240]]
random forest 

In [83]:
# running Stochastic Gradient Descent model
# we will run it for ten times, then get
i = 0
average_acc = 0
average_fscore = 0
while i < 10:
    print (i)
    traing_df, test_df = read_data(i)
    shffule_traing_df = shuffle(traing_df)
    shffule_test_df = shuffle(test_df)
    features = traing_df.columns[1:17]
    # print(features)
    X_train = shffule_traing_df[features]
    y_train = shffule_traing_df['Label']

    X_test = shffule_test_df[features]
    y_test = shffule_test_df['Label']
    
    clf_sgd = SGDClassifier()
    clf_sgd.fit(X_train, y_train)
    y_pred_sgd = clf_sgd.predict(X_test)
    acc_sgd = accuracy_score(y_test, y_pred_sgd)
    f_score = f1_score(y_test, y_pred_sgd, average='weighted')
    average_acc += acc_sgd
    average_fscore += f_score
    print ("stochastic gradient descent accuracy: ",acc_sgd)
    print ("stochastic gradient descent F-score: ",f_score)
    print (confusion_matrix(y_test, y_pred_sgd))

    con_matrix = []
    con_matrix = confusion_matrix(y_test, y_pred_sgd)
    P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
    print ("stochastic gradient descent accuracy of precision true: ",P_true)
    P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
    print ("stochastic gradient descent accuracy of precision false: ",P_false)
    i+=1
average_acc = average_acc/10
average_fscore = average_fscore/10

print ("Average stochastic gradient descent accuracy: ",average_acc)
print ("Average stochastic gradient descent F-score: ",average_fscore)




0


/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/ipykernel_launcher.py:32: RuntimeWarning: invalid value encountered in long_scalars


stochastic gradient descent accuracy:  0.632315521628
stochastic gradient descent F-score:  0.489884355806
[[  0 289]
 [  0 497]]
stochastic gradient descent accuracy of precision true:  nan
stochastic gradient descent accuracy of precision false:  0.632315521628
1
stochastic gradient descent accuracy:  0.585365853659
stochastic gradient descent F-score:  0.432270168856
[[  0 306]
 [  0 432]]
stochastic gradient descent accuracy of precision true:  nan
stochastic gradient descent accuracy of precision false:  0.585365853659
2
stochastic gradient descent accuracy:  0.620134228188
stochastic gradient descent F-score:  0.474734073609
[[  0 283]
 [  0 462]]
stochastic gradient descent accuracy of precision true:  nan
stochastic gradient descent accuracy of precision false:  0.620134228188
3
stochastic gradient descent accuracy:  0.396153846154
stochastic gradient descent F-score:  0.22481457936
[[309   0]
 [471   0]]
stochastic gradient descent accuracy of precision true:  0.396153846154
s

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/ipykernel_launcher.py:34: RuntimeWarning: invalid value encountered in long_scalars


stochastic gradient descent accuracy:  0.607541899441
stochastic gradient descent F-score:  0.489242485135
[[ 14 269]
 [ 12 421]]
stochastic gradient descent accuracy of precision true:  0.538461538462
stochastic gradient descent accuracy of precision false:  0.610144927536
5
stochastic gradient descent accuracy:  0.584487534626
stochastic gradient descent F-score:  0.43121283149
[[  0 300]
 [  0 422]]
stochastic gradient descent accuracy of precision true:  nan
stochastic gradient descent accuracy of precision false:  0.584487534626
6
stochastic gradient descent accuracy:  0.367701863354
stochastic gradient descent F-score:  0.19771072035
[[296   0]
 [509   0]]
stochastic gradient descent accuracy of precision true:  0.367701863354
stochastic gradient descent accuracy of precision false:  nan
7
stochastic gradient descent accuracy:  0.595505617978
stochastic gradient descent F-score:  0.444532362716
[[  0 288]
 [  0 424]]
stochastic gradient descent accuracy of precision true:  nan
st

In [84]:
# running AdaBoostClassifier model
# we will run it for ten times, then get
i = 0
average_acc = 0
average_fscore = 0
while i < 10:
    print (i)
    traing_df, test_df = read_data(i)
    shffule_traing_df = shuffle(traing_df)
    shffule_test_df = shuffle(test_df)
    features = traing_df.columns[1:17]
    # print(features)
    X_train = shffule_traing_df[features]
    y_train = shffule_traing_df['Label']

    X_test = shffule_test_df[features]
    y_test = shffule_test_df['Label']
    
    clf_ada = AdaBoostClassifier()
    clf_ada.fit(X_train, y_train)
    y_pred_ada = clf_ada.predict(X_test)
    acc_ada = accuracy_score(y_test, y_pred_ada)
    f_score = f1_score(y_test, y_pred_ada, average='weighted')
    average_acc += acc_ada
    average_fscore += f_score
    print ("AdaBoost accuracy: ",acc_ada)
    print ("AdaBoost F-score: ",f_score)
    print (confusion_matrix(y_test, y_pred_ada))

    con_matrix = []
    con_matrix = confusion_matrix(y_test, y_pred_ada)
    P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
    print ("AdaBoost accuracy of precision true: ",P_true)
    P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
    print ("AdaBoost accuracy of precision false: ",P_false)
    i += 1
average_acc = average_acc/10
average_fscore = average_fscore/10

print ("Average AdaBoost accuracy: ",average_acc)
print ("Average AdaBoost F-score: ",average_fscore)

0
AdaBoost accuracy:  0.617048346056
AdaBoost F-score:  0.578185251269
[[ 67 222]
 [ 79 418]]
AdaBoost accuracy of precision true:  0.458904109589
AdaBoost accuracy of precision false:  0.653125
1
AdaBoost accuracy:  0.536585365854
AdaBoost F-score:  0.49176881572
[[ 56 250]
 [ 92 340]]
AdaBoost accuracy of precision true:  0.378378378378
AdaBoost accuracy of precision false:  0.576271186441
2
AdaBoost accuracy:  0.591946308725
AdaBoost F-score:  0.571478695922
[[ 86 197]
 [107 355]]
AdaBoost accuracy of precision true:  0.445595854922
AdaBoost accuracy of precision false:  0.643115942029
3
AdaBoost accuracy:  0.566666666667
AdaBoost F-score:  0.518570570571
[[ 56 253]
 [ 85 386]]
AdaBoost accuracy of precision true:  0.397163120567
AdaBoost accuracy of precision false:  0.60406885759
4
AdaBoost accuracy:  0.603351955307
AdaBoost F-score:  0.576402525216
[[ 84 199]
 [ 85 348]]
AdaBoost accuracy of precision true:  0.497041420118
AdaBoost accuracy of precision false:  0.636197440585
5
A

In [85]:
# running Nearest Neighbors model
# we will run it for ten times, then get
i = 0
average_acc = 0
average_fscore = 0
while i < 10:
    print (i)
    traing_df, test_df = read_data(i)
    shffule_traing_df = shuffle(traing_df)
    shffule_test_df = shuffle(test_df)
    features = traing_df.columns[1:17]
    # print(features)
    X_train = shffule_traing_df[features]
    y_train = shffule_traing_df['Label']

    X_test = shffule_test_df[features]
    y_test = shffule_test_df['Label']
    
    clf_knn = KNeighborsClassifier()
    clf_knn.fit(X_train, y_train)
    y_pred_knn = clf_knn.predict(X_test)
    acc_knn = accuracy_score(y_test, y_pred_knn)
    f_score = f1_score(y_test, y_pred_knn, average='weighted')
    average_acc += acc_knn
    average_fscore += f_score
    print ("k nearest neighbors accuracy: ",acc_knn)
    print ("k nearest neighbors F-score: ",f_score)
    print (confusion_matrix(y_test, y_pred_knn))

    con_matrix = []
    con_matrix = confusion_matrix(y_test, y_pred_knn)
    P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
    print ("k nearest neighbors accuracy of precision true: ",P_true)
    P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
    print ("k nearest neighbors accuracy of precision false: ",P_false)
    i += 1

average_acc = average_acc/10
average_fscore = average_fscore/10

print ("Average k nearest neighbors accuracy: ",average_acc)
print ("Average k nearest neighbors F-score: ",average_fscore)
   


0
k nearest neighbors accuracy:  0.516539440204
k nearest neighbors F-score:  0.517224128698
[[101 188]
 [192 305]]
k nearest neighbors accuracy of precision true:  0.344709897611
k nearest neighbors accuracy of precision false:  0.618661257606
1
k nearest neighbors accuracy:  0.547425474255
k nearest neighbors F-score:  0.542682127987
[[122 184]
 [150 282]]
k nearest neighbors accuracy of precision true:  0.448529411765
k nearest neighbors accuracy of precision false:  0.605150214592
2
k nearest neighbors accuracy:  0.510067114094
k nearest neighbors F-score:  0.507311538119
[[ 93 190]
 [175 287]]
k nearest neighbors accuracy of precision true:  0.347014925373
k nearest neighbors accuracy of precision false:  0.601677148847
3
k nearest neighbors accuracy:  0.521794871795
k nearest neighbors F-score:  0.51991193005
[[116 193]
 [180 291]]
k nearest neighbors accuracy of precision true:  0.391891891892
k nearest neighbors accuracy of precision false:  0.601239669421
4
k nearest neighbors

In [86]:
# running GradientBoosting model
# we will run it for ten times, then get
i = 0
average_acc = 0
average_fscore = 0
while i < 10:
    print (i)
    traing_df, test_df = read_data(i)
    shffule_traing_df = shuffle(traing_df)
    shffule_test_df = shuffle(test_df)
    features = traing_df.columns[1:17]
    # print(features)
    X_train = shffule_traing_df[features]
    y_train = shffule_traing_df['Label']

    X_test = shffule_test_df[features]
    y_test = shffule_test_df['Label']
    
    clf_gdb = GradientBoostingClassifier()
    clf_gdb.fit(X_train, y_train)
    y_pred_gdb = clf_gdb.predict(X_test)
    acc_gdb = accuracy_score(y_test, y_pred_gdb)
    f_score = f1_score(y_test, y_pred_gdb, average='weighted')
    average_acc += acc_gdb
    average_fscore += f_score
    print ("GradientBoosting accuracy: ",acc_gdb)
    print (confusion_matrix(y_test, y_pred_gdb))

    con_matrix = []
    con_matrix = confusion_matrix(y_test, y_pred_gdb)
    P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
    print ("GradientBoosting accuracy of precision true: ",P_true)
    P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
    print ("GradientBoosting accuracy of precision false: ",P_false)
    i += 1

average_acc = average_acc/10
average_fscore = average_fscore/10

print ("Average GradientBoosting accuracy: ",average_acc)
print ("Average GradientBoosting F-score: ",average_fscore)

0
GradientBoosting accuracy:  0.596692111959
[[ 54 235]
 [ 82 415]]
GradientBoosting accuracy of precision true:  0.397058823529
GradientBoosting accuracy of precision false:  0.638461538462
1
GradientBoosting accuracy:  0.543360433604
[[ 68 238]
 [ 99 333]]
GradientBoosting accuracy of precision true:  0.407185628743
GradientBoosting accuracy of precision false:  0.583187390543
2
GradientBoosting accuracy:  0.579865771812
[[ 70 213]
 [100 362]]
GradientBoosting accuracy of precision true:  0.411764705882
GradientBoosting accuracy of precision false:  0.629565217391
3
GradientBoosting accuracy:  0.575641025641
[[ 41 268]
 [ 63 408]]
GradientBoosting accuracy of precision true:  0.394230769231
GradientBoosting accuracy of precision false:  0.603550295858
4
GradientBoosting accuracy:  0.614525139665
[[ 67 216]
 [ 60 373]]
GradientBoosting accuracy of precision true:  0.527559055118
GradientBoosting accuracy of precision false:  0.633276740238
5
GradientBoosting accuracy:  0.548476454294


# Follow UvA-NEMO Protocol, Train on 1 folds, Test on 9 fold.

In [78]:
# running linear SVM model
# we will run it for ten times, then get
i = 0
average_acc = 0
average_fscore = 0
while i < 10:
    print (i)
    traing_df, test_df = read_data(i)
    shffule_traing_df = shuffle(test_df)
    shffule_test_df = shuffle(traing_df)
    features = traing_df.columns[1:17]
    # print(features)
    X_train = shffule_traing_df[features]
    y_train = shffule_traing_df['Label']

    X_test = shffule_test_df[features]
    y_test = shffule_test_df['Label']
    
    clf_svm = LinearSVC()
    clf_svm.fit(X_train, y_train)
    y_pred_svm = clf_svm.predict(X_test)
    acc_svm = accuracy_score(y_test, y_pred_svm)
    f_score = f1_score(y_test, y_pred_svm, average='weighted')
    average_acc += acc_svm
    average_fscore += f_score
    print ("Linear SVM accuracy: ",acc_svm)
    print ("Linear SVM F-score: ",f_score)
    print (confusion_matrix(y_test, y_pred_svm))
    
    con_matrix = []
    con_matrix = confusion_matrix(y_test, y_pred_svm)
    P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
    print ("Linear SVM accuracy of precision true: ",P_true)
    P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
    print ("Linear SVM accuracy of precision false: ",P_false)
    
    i += 1

average_acc = average_acc/10
average_fscore = average_fscore/10

print ("Average Linear SVM accuracy: ",average_acc)
print ("Average SVM F-score: ",average_fscore)


0
Linear SVM accuracy:  0.583558594371
Linear SVM F-score:  0.449082304984
[[  74 2554]
 [  65 3596]]
Linear SVM accuracy of precision true:  0.532374100719
Linear SVM accuracy of precision false:  0.584715447154
1
Linear SVM accuracy:  0.412182420704
Linear SVM F-score:  0.24079753299
[[2611    0]
 [3725    1]]
Linear SVM accuracy of precision true:  0.412089646465
Linear SVM accuracy of precision false:  1.0
2
Linear SVM accuracy:  0.583886255924
Linear SVM F-score:  0.432192766153
[[   6 2628]
 [   6 3690]]
Linear SVM accuracy of precision true:  0.5
Linear SVM accuracy of precision false:  0.584045584046
3
Linear SVM accuracy:  0.585226370135
Linear SVM F-score:  0.435858102739
[[  12 2596]
 [  15 3672]]
Linear SVM accuracy of precision true:  0.444444444444
Linear SVM accuracy of precision false:  0.585832801532
4
Linear SVM accuracy:  0.58546941343
Linear SVM F-score:  0.432910819926
[[   1 2633]
 [   3 3722]]
Linear SVM accuracy of precision true:  0.25
Linear SVM accuracy of pr

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/ipykernel_launcher.py:34: RuntimeWarning: invalid value encountered in long_scalars


Linear SVM accuracy:  0.413169888417
Linear SVM F-score:  0.241597783952
[[2629    0]
 [3734    0]]
Linear SVM accuracy of precision true:  0.413169888417
Linear SVM accuracy of precision false:  nan
8
Linear SVM accuracy:  0.412141073658
Linear SVM F-score:  0.240571240033
[[2641    0]
 [3767    0]]
Linear SVM accuracy of precision true:  0.412141073658
Linear SVM accuracy of precision false:  nan
9
Linear SVM accuracy:  0.416732688956
Linear SVM F-score:  0.245164293022
[[2630    0]
 [3681    0]]
Linear SVM accuracy of precision true:  0.416732688956
Linear SVM accuracy of precision false:  nan
Average Linear SVM accuracy:  0.516225351641
Average SVM F-score:  0.360507448185


In [87]:
# running random forest model
# we will run it for ten times, then get
i = 0
average_acc = 0
average_fscore = 0
while i < 10:
    print (i)
    traing_df, test_df = read_data(i)
    shffule_traing_df = shuffle(test_df)
    shffule_test_df = shuffle(traing_df)
    features = traing_df.columns[1:17]
    # print(features)
    X_train = shffule_traing_df[features]
    y_train = shffule_traing_df['Label']

    X_test = shffule_test_df[features]
    y_test = shffule_test_df['Label']
    
    clf_rf = RandomForestClassifier()
    clf_rf.fit(X_train, y_train)
    y_pred_rf = clf_rf.predict(X_test)
    acc_rf = accuracy_score(y_test, y_pred_rf)
    f_score = f1_score(y_test, y_pred_rf, average='weighted')
    average_acc += acc_rf
    average_fscore += f_score
    print ("random forest accuracy: ",acc_rf)
    print ("random forest F-score: ",f_score)
    print (confusion_matrix(y_test, y_pred_rf))

    con_matrix = []
    con_matrix = confusion_matrix(y_test, y_pred_rf)
    P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
    print ("random forest accuracy of precision true: ",P_true)
    P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
    print ("random forest accuracy of precision false: ",P_false)
    
    i += 1

average_acc = average_acc/10
average_fscore = average_fscore/10

print ("Average random forest accuracy: ",average_acc)
print ("Average random forest F-score: ",average_fscore)


0
random forest accuracy:  0.511369057084
random forest F-score:  0.511588158711
[[1100 1528]
 [1545 2116]]
random forest accuracy of precision true:  0.415879017013
random forest accuracy of precision false:  0.580680570801
1
random forest accuracy:  0.511598548209
random forest F-score:  0.515226256517
[[1279 1332]
 [1763 1963]]
random forest accuracy of precision true:  0.420447074293
random forest accuracy of precision false:  0.595751138088
2
random forest accuracy:  0.503159557662
random forest F-score:  0.506638644704
[[1296 1338]
 [1807 1889]]
random forest accuracy of precision true:  0.417660328714
random forest accuracy of precision false:  0.585373411838
3
random forest accuracy:  0.514058776807
random forest F-score:  0.514180381681
[[1083 1525]
 [1534 2153]]
random forest accuracy of precision true:  0.413832632786
random forest accuracy of precision false:  0.585372485046
4
random forest accuracy:  0.521465639251
random forest F-score:  0.523890120927
[[1230 1404]
 [1639

In [92]:
# running Stochastic Gradient Descent model
# we will run it for ten times, then get
i = 0
average_acc = 0
average_fscore = 0
while i < 10:
    print (i)
    traing_df, test_df = read_data(i)
    shffule_traing_df = shuffle(test_df)
    shffule_test_df = shuffle(traing_df)
    features = traing_df.columns[1:17]
    # print(features)
    X_train = shffule_traing_df[features]
    y_train = shffule_traing_df['Label']

    X_test = shffule_test_df[features]
    y_test = shffule_test_df['Label']
    
    clf_sgd = SGDClassifier()
    clf_sgd.fit(X_train, y_train)
    y_pred_sgd = clf_sgd.predict(X_test)
    acc_sgd = accuracy_score(y_test, y_pred_sgd)
    f_score = f1_score(y_test, y_pred_sgd, average='weighted')
    average_acc += acc_sgd
    average_fscore += f_score
    print ("stochastic gradient descent accuracy: ",acc_sgd)
    print ("stochastic gradient descent F-score: ",f_score)
    print (confusion_matrix(y_test, y_pred_sgd))

    con_matrix = []
    con_matrix = confusion_matrix(y_test, y_pred_sgd)
    P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
    print ("stochastic gradient descent accuracy of precision true: ",P_true)
    P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
    print ("stochastic gradient descent accuracy of precision false: ",P_false)
    i+=1
average_acc = average_acc/10
average_fscore = average_fscore/10

print ("Average stochastic gradient descent accuracy: ",average_acc)
print ("Average stochastic gradient descent F-score: ",average_fscore)

0


/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)


stochastic gradient descent accuracy:  0.582604547623
stochastic gradient descent F-score:  0.431730406651
[[  11 2617]
 [   8 3653]]
stochastic gradient descent accuracy of precision true:  0.578947368421
stochastic gradient descent accuracy of precision false:  0.582615629984
1


/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/ipykernel_launcher.py:34: RuntimeWarning: invalid value encountered in long_scalars


stochastic gradient descent accuracy:  0.412024617327
stochastic gradient descent F-score:  0.240455135414
[[2611    0]
 [3726    0]]
stochastic gradient descent accuracy of precision true:  0.412024617327
stochastic gradient descent accuracy of precision false:  nan
2
stochastic gradient descent accuracy:  0.416113744076
stochastic gradient descent F-score:  0.24454341854
[[2634    0]
 [3696    0]]
stochastic gradient descent accuracy of precision true:  0.416113744076
stochastic gradient descent accuracy of precision false:  nan
3
stochastic gradient descent accuracy:  0.41429706116
stochastic gradient descent F-score:  0.242724190836
[[2608    0]
 [3687    0]]
stochastic gradient descent accuracy of precision true:  0.41429706116
stochastic gradient descent accuracy of precision false:  nan
4
stochastic gradient descent accuracy:  0.585783928291
stochastic gradient descent F-score:  0.432773727267
[[   0 2634]
 [   0 3725]]
stochastic gradient descent accuracy of precision true:  na

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/ipykernel_launcher.py:32: RuntimeWarning: invalid value encountered in long_scalars


stochastic gradient descent accuracy:  0.587911223044
stochastic gradient descent F-score:  0.435455259574
[[   0 2617]
 [   1 3735]]
stochastic gradient descent accuracy of precision true:  0.0
stochastic gradient descent accuracy of precision false:  0.588003778338
6
stochastic gradient descent accuracy:  0.581977671451
stochastic gradient descent F-score:  0.428195689712
[[   0 2621]
 [   0 3649]]
stochastic gradient descent accuracy of precision true:  nan
stochastic gradient descent accuracy of precision false:  0.581977671451
7
stochastic gradient descent accuracy:  0.586830111583
stochastic gradient descent F-score:  0.43403459179
[[   0 2629]
 [   0 3734]]
stochastic gradient descent accuracy of precision true:  nan
stochastic gradient descent accuracy of precision false:  0.586830111583
8
stochastic gradient descent accuracy:  0.587858926342
stochastic gradient descent F-score:  0.435275592242
[[   0 2641]
 [   0 3767]]
stochastic gradient descent accuracy of precision true:  

In [91]:
# running AdaBoostClassifier model
# we will run it for ten times, then get
i = 0
average_acc = 0
average_fscore = 0
while i < 10:
    print (i)
    traing_df, test_df = read_data(i)
    shffule_traing_df = shuffle(test_df)
    shffule_test_df = shuffle(traing_df)
    features = traing_df.columns[1:17]
    # print(features)
    X_train = shffule_traing_df[features]
    y_train = shffule_traing_df['Label']

    X_test = shffule_test_df[features]
    y_test = shffule_test_df['Label']
    
    clf_ada = AdaBoostClassifier()
    clf_ada.fit(X_train, y_train)
    y_pred_ada = clf_ada.predict(X_test)
    acc_ada = accuracy_score(y_test, y_pred_ada)
    f_score = f1_score(y_test, y_pred_ada, average='weighted')
    average_acc += acc_ada
    average_fscore += f_score
    print ("AdaBoost accuracy: ",acc_ada)
    print ("AdaBoost F-score: ",f_score)
    print (confusion_matrix(y_test, y_pred_ada))

    con_matrix = []
    con_matrix = confusion_matrix(y_test, y_pred_ada)
    P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
    print ("AdaBoost accuracy of precision true: ",P_true)
    P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
    print ("AdaBoost accuracy of precision false: ",P_false)
    i += 1
average_acc = average_acc/10
average_fscore = average_fscore/10

print ("Average AdaBoost accuracy: ",average_acc)
print ("Average AdaBoost F-score: ",average_fscore)

0
AdaBoost accuracy:  0.542375576403
AdaBoost F-score:  0.533607195922
[[ 952 1676]
 [1202 2459]]
AdaBoost accuracy of precision true:  0.441968430826
AdaBoost accuracy of precision false:  0.594679564692
1
AdaBoost accuracy:  0.511440744832
AdaBoost F-score:  0.51055249981
[[1033 1578]
 [1518 2208]]
AdaBoost accuracy of precision true:  0.404939239514
AdaBoost accuracy of precision false:  0.583201267829
2
AdaBoost accuracy:  0.495734597156
AdaBoost F-score:  0.497626075844
[[1120 1514]
 [1678 2018]]
AdaBoost accuracy of precision true:  0.400285918513
AdaBoost accuracy of precision false:  0.571347678369
3
AdaBoost accuracy:  0.54058776807
AdaBoost F-score:  0.524700194559
[[ 809 1799]
 [1093 2594]]
AdaBoost accuracy of precision true:  0.425341745531
AdaBoost accuracy of precision false:  0.590484862281
4
AdaBoost accuracy:  0.536719610002
AdaBoost F-score:  0.534231784624
[[1078 1556]
 [1390 2335]]
AdaBoost accuracy of precision true:  0.436790923825
AdaBoost accuracy of precision 

In [93]:
# running Nearest Neighbors model
# we will run it for ten times, then get
i = 0
average_acc = 0
average_fscore = 0
while i < 10:
    print (i)
    traing_df, test_df = read_data(i)
    shffule_traing_df = shuffle(test_df)
    shffule_test_df = shuffle(traing_df)
    features = traing_df.columns[1:17]
    # print(features)
    X_train = shffule_traing_df[features]
    y_train = shffule_traing_df['Label']

    X_test = shffule_test_df[features]
    y_test = shffule_test_df['Label']
    
    clf_knn = KNeighborsClassifier()
    clf_knn.fit(X_train, y_train)
    y_pred_knn = clf_knn.predict(X_test)
    acc_knn = accuracy_score(y_test, y_pred_knn)
    f_score = f1_score(y_test, y_pred_knn, average='weighted')
    average_acc += acc_knn
    average_fscore += f_score
    print ("k nearest neighbors accuracy: ",acc_knn)
    print ("k nearest neighbors F-score: ",f_score)
    print (confusion_matrix(y_test, y_pred_knn))

    con_matrix = []
    con_matrix = confusion_matrix(y_test, y_pred_knn)
    P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
    print ("k nearest neighbors accuracy of precision true: ",P_true)
    P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
    print ("k nearest neighbors accuracy of precision false: ",P_false)
    i += 1

average_acc = average_acc/10
average_fscore = average_fscore/10

print ("Average k nearest neighbors accuracy: ",average_acc)
print ("Average k nearest neighbors F-score: ",average_fscore)

0
k nearest neighbors accuracy:  0.505803784385
k nearest neighbors F-score:  0.506995802916
[[1124 1504]
 [1604 2057]]
k nearest neighbors accuracy of precision true:  0.412023460411
k nearest neighbors accuracy of precision false:  0.577646728447
1
k nearest neighbors accuracy:  0.526274262269
k nearest neighbors F-score:  0.525912576543
[[1097 1514]
 [1488 2238]]
k nearest neighbors accuracy of precision true:  0.424371373308
k nearest neighbors accuracy of precision false:  0.596481876333
2
k nearest neighbors accuracy:  0.508530805687
k nearest neighbors F-score:  0.509834468728
[[1133 1501]
 [1610 2086]]
k nearest neighbors accuracy of precision true:  0.413051403573
k nearest neighbors accuracy of precision false:  0.581544466128
3
k nearest neighbors accuracy:  0.5104050834
k nearest neighbors F-score:  0.505730934261
[[ 933 1675]
 [1407 2280]]
k nearest neighbors accuracy of precision true:  0.398717948718
k nearest neighbors accuracy of precision false:  0.576485461441
4
k ne

In [94]:
# running GradientBoosting model
# we will run it for ten times, then get
i = 0
average_acc = 0
average_fscore = 0
while i < 10:
    print (i)
    traing_df, test_df = read_data(i)
    shffule_traing_df = shuffle(test_df)
    shffule_test_df = shuffle(traing_df)
    features = traing_df.columns[1:17]
    # print(features)
    X_train = shffule_traing_df[features]
    y_train = shffule_traing_df['Label']

    X_test = shffule_test_df[features]
    y_test = shffule_test_df['Label']
    
    clf_gdb = GradientBoostingClassifier()
    clf_gdb.fit(X_train, y_train)
    y_pred_gdb = clf_gdb.predict(X_test)
    acc_gdb = accuracy_score(y_test, y_pred_gdb)
    f_score = f1_score(y_test, y_pred_gdb, average='weighted')
    average_acc += acc_gdb
    average_fscore += f_score
    print ("GradientBoosting accuracy: ",acc_gdb)
    print (confusion_matrix(y_test, y_pred_gdb))

    con_matrix = []
    con_matrix = confusion_matrix(y_test, y_pred_gdb)
    P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
    print ("GradientBoosting accuracy of precision true: ",P_true)
    P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
    print ("GradientBoosting accuracy of precision false: ",P_false)
    i += 1

average_acc = average_acc/10
average_fscore = average_fscore/10

print ("Average GradientBoosting accuracy: ",average_acc)
print ("Average GradientBoosting F-score: ",average_fscore)

0
GradientBoosting accuracy:  0.531722054381
[[ 820 1808]
 [1137 2524]]
GradientBoosting accuracy of precision true:  0.419008686765
GradientBoosting accuracy of precision false:  0.582640812558
1
GradientBoosting accuracy:  0.54615748777
[[1023 1588]
 [1288 2438]]
GradientBoosting accuracy of precision true:  0.442665512765
GradientBoosting accuracy of precision false:  0.605563835072
2
GradientBoosting accuracy:  0.500631911532
[[1067 1567]
 [1594 2102]]
GradientBoosting accuracy of precision true:  0.400977076287
GradientBoosting accuracy of precision false:  0.572908149359
3
GradientBoosting accuracy:  0.542176330421
[[ 709 1899]
 [ 983 2704]]
GradientBoosting accuracy of precision true:  0.419030732861
GradientBoosting accuracy of precision false:  0.587442971975
4
GradientBoosting accuracy:  0.546626828118
[[1015 1619]
 [1264 2461]]
GradientBoosting accuracy of precision true:  0.445370776656
GradientBoosting accuracy of precision false:  0.60318627451
5
GradientBoosting accuracy

# USING DIFFERENT CROSS VALIDATION METHOD

In [33]:
# load deliberate training data set
import glob
deli_training_path = 'file-video-stream/videos/deliberate/aggregated_30_results/training_set/'
deli_allFiles = glob.glob(deli_training_path + "/*.csv")
deli_training_df = pd.DataFrame()
list_ = []
for file_ in deli_allFiles:
    df = pd.read_csv(file_)
    list_.append(df)

deli_training_df = pd.concat(list_)

# add label = 0
deli_training_df['Label'] = 0
deli_training_df.head()
# print(deli_training_df.count)

Unnamed: 0          A         B          C          D          E  \
0           1  10.013755  9.166800  15.650131  74.795202  66.356137   
1           2   9.974192  9.238299  14.502745  74.287629  64.823098   
2           3   9.666960  9.355971  14.313919  74.909143  64.853508   
3           4   9.979202  9.288829  14.465512  74.877653  64.945828   
4           5  10.256312  9.340281  14.411810  75.324658  65.680890   

           F          G          H       SD1       SD2       SD3       SD4  \
0  65.834354  10.814182  10.086911  0.507971  0.412039  0.820605  0.666678   
1  64.519960  11.066618  10.084197  0.464212  0.392217  0.661093  0.617705   
2  64.729124  10.752747   9.992751  0.428029  0.407197  0.667119  0.503644   
3  64.564075  10.912623  10.180831  0.426833  0.343019  0.618298  0.685874   
4  65.274564  10.831709  10.140511  0.328720  0.354702  0.407933  0.442563   

        SD5       SD6       SD7       SD8  Label  
0  1.600961  1.561363  0.391753  0.536244      0  
1  1.402138  1.281179  0.443435  0.419095      0  
2  0.767531  0.860492  0.280059  0.494909      0  
3  1.003029  1.160551  0.463311  0.428973      0  
4  0.787872  0.705650  0.327740  0.450964      0

In [34]:
# load spontanenous training data set
# import glob
spon_training_path = 'file-video-stream/videos/spontaneous/aggregated_30_results/training_set/'
spon_allFiles = glob.glob(spon_training_path + "/*.csv")
spon_training_df = pd.DataFrame()
list_ = []
for file_ in spon_allFiles:
    df = pd.read_csv(file_)
    list_.append(df)

spon_training_df = pd.concat(list_)

# add label = 1
spon_training_df['Label'] = 1
spon_training_df.head()

Unnamed: 0          A          B          C          D           E  \
0           1  12.927323  13.399970  24.121134  96.012829   98.186468   
1           2  11.206087  13.478276  32.288767  96.374934  100.585190   
2           3  11.546581  13.254397  30.539609  96.430829   99.968338   
3           4  11.660340  13.245007  28.664035  96.291502   99.419740   
4           5  11.636178  13.091032  27.530803  96.547495   98.488517   

           F          G          H       SD1       SD2       SD3       SD4  \
0  90.634207  12.504202  11.559298  0.785912  0.554502  2.938975  0.635037   
1  90.647308  12.132997   9.955390  0.351585  0.485874  0.754233  0.521576   
2  90.813604  12.256558  10.385677  0.458032  0.392808  1.548850  0.511822   
3  91.393371  12.522012  10.858429  0.486279  0.190919  0.860084  0.529077   
4  91.446388  12.674371  11.108569  0.482385  0.437671  0.623064  0.530321   

        SD5       SD6       SD7       SD8  Label  
0  1.901981  1.845875  0.527517  0.562109      1  
1  0.502967  0.815821  0.153998  0.238488      1  
2  0.514508  0.537844  0.331828  0.452085      1  
3  0.530933  0.593146  0.446326  0.441043      1  
4  0.527959  0.474088  0.400389  0.407870      1

In [35]:
print(spon_training_df.count)

<bound method DataFrame.count of     Unnamed: 0          A          B          C          D           E  \
0            1  12.927323  13.399970  24.121134  96.012829   98.186468   
1            2  11.206087  13.478276  32.288767  96.374934  100.585190   
2            3  11.546581  13.254397  30.539609  96.430829   99.968338   
3            4  11.660340  13.245007  28.664035  96.291502   99.419740   
4            5  11.636178  13.091032  27.530803  96.547495   98.488517   
5            6  11.630859  12.887032  27.193026  96.374331   98.677792   
6            7  12.152010  12.847672  26.914035  96.025775   98.283058   
7            8  11.946614  12.998536  26.752888  96.539911   98.588543   
8            9  11.872450  13.205587  27.066805  96.427276   98.931224   
9           10  11.990754  13.043669  27.825677  96.594046   98.750842   
0            1   9.304773   8.431064  13.551589  73.001367   66.198216   
1            2   9.664341   8.775675  12.842487  73.772550   67.509434   
2    

In [36]:
# merge two training data set
traing_list = [spon_training_df, deli_training_df]
traing_df = pd.concat(traing_list)
print(traing_df.count)

<bound method DataFrame.count of     Unnamed: 0          A          B          C           D           E  \
0            1  12.927323  13.399970  24.121134   96.012829   98.186468   
1            2  11.206087  13.478276  32.288767   96.374934  100.585190   
2            3  11.546581  13.254397  30.539609   96.430829   99.968338   
3            4  11.660340  13.245007  28.664035   96.291502   99.419740   
4            5  11.636178  13.091032  27.530803   96.547495   98.488517   
5            6  11.630859  12.887032  27.193026   96.374331   98.677792   
6            7  12.152010  12.847672  26.914035   96.025775   98.283058   
7            8  11.946614  12.998536  26.752888   96.539911   98.588543   
8            9  11.872450  13.205587  27.066805   96.427276   98.931224   
9           10  11.990754  13.043669  27.825677   96.594046   98.750842   
0            1   9.304773   8.431064  13.551589   73.001367   66.198216   
1            2   9.664341   8.775675  12.842487   73.772550   67.50

In [37]:
# set input X values
features = traing_df.columns[1:17]
# print(features)
X = traing_df[features]
y = traing_df['Label']
X_train, X_test, y_train, y_test = cross_validation.train_test_split(X/10.,y,test_size=0.1,random_state=0)

# Cross Validation Data, Train : Test = 9:1

In [38]:
# running linear SVM model
clf_svm = LinearSVC()
clf_svm.fit(X_train, y_train)
y_pred_svm = clf_svm.predict(X_test)
acc_svm = accuracy_score(y_test, y_pred_svm)
print ("Linear SVM accuracy: ",acc_svm)
print (confusion_matrix(y_test, y_pred_svm))

con_matrix = []
con_matrix = confusion_matrix(y_test, y_pred_svm)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("Linear SVM accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("Linear SVM accuracy of precision false: ",P_false)

Linear SVM accuracy:  0.585959885387
[[ 13 281]
 [  8 396]]
Linear SVM accuracy of precision true:  0.619047619048
Linear SVM accuracy of precision false:  0.584933530281


In [39]:
# running random forest model
clf_rf = RandomForestClassifier()
clf_rf.fit(X_train, y_train)
y_pred_rf = clf_rf.predict(X_test)
acc_rf = accuracy_score(y_test, y_pred_rf)
print ("random forest accuracy: ",acc_rf)
print (confusion_matrix(y_test, y_pred_rf))

con_matrix = []
con_matrix = confusion_matrix(y_test, y_pred_rf)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("random forest accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("random forest accuracy of precision false: ",P_false)

random forest accuracy:  0.626074498567
[[168 126]
 [135 269]]
random forest accuracy of precision true:  0.554455445545
random forest accuracy of precision false:  0.681012658228


In [40]:
# running Stochastic Gradient Descent model
clf_sgd = SGDClassifier()
clf_sgd.fit(X_train, y_train)
y_pred_sgd = clf_sgd.predict(X_test)
acc_sgd = accuracy_score(y_test, y_pred_sgd)
print ("stochastic gradient descent accuracy: ",acc_sgd)
print (confusion_matrix(y_test, y_pred_sgd))

con_matrix = []
con_matrix = confusion_matrix(y_test, y_pred_sgd)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("stochastic gradient descent accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("stochastic gradient descent accuracy of precision false: ",P_false)

stochastic gradient descent accuracy:  0.578796561605
[[  0 294]
 [  0 404]]
stochastic gradient descent accuracy of precision true:  nan
stochastic gradient descent accuracy of precision false:  0.578796561605


/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/ipykernel_launcher.py:11: RuntimeWarning: invalid value encountered in long_scalars
  # This is added back by InteractiveShellApp.init_path()


In [54]:
# running AdaBoostClassifier model
clf_ada = AdaBoostClassifier()
clf_ada.fit(X_train, y_train)
y_pred_ada = clf_ada.predict(X_test)
acc_ada = accuracy_score(y_test, y_pred_ada)
print ("AdaBoost accuracy: ",acc_ada)
print (confusion_matrix(y_test, y_pred_ada))

con_matrix = []
con_matrix = confusion_matrix(y_test, y_pred_ada)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("AdaBoost accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("AdaBoost accuracy of precision false: ",P_false)

AdaBoost accuracy:  0.565902578797
[[ 59 235]
 [ 68 336]]
AdaBoost accuracy of precision true:  0.464566929134
AdaBoost accuracy of precision false:  0.588441330998


In [42]:
# running Nearest Neighbors model
clf_knn = KNeighborsClassifier()
clf_knn.fit(X_train, y_train)
y_pred_knn = clf_knn.predict(X_test)
acc_knn = accuracy_score(y_test, y_pred_knn)
print ("nearest neighbors accuracy: ",acc_knn)
print (confusion_matrix(y_test, y_pred_knn))

con_matrix = []
con_matrix = confusion_matrix(y_test, y_pred_knn)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("k nearest neighbors accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("k nearest neighbors accuracy of precision false: ",P_false)

nearest neighbors accuracy:  0.829512893983
[[224  70]
 [ 49 355]]
k nearest neighbors accuracy of precision true:  0.820512820513
k nearest neighbors accuracy of precision false:  0.835294117647


In [44]:
# running GradientBoosting model
clf_gdb = GradientBoostingClassifier()
clf_gdb.fit(X_train, y_train)
y_pred_gdb = clf_gdb.predict(X_test)
acc_gdb = accuracy_score(y_test, y_pred_gdb)
print ("GradientBoosting accuracy: ",acc_gdb)
print (confusion_matrix(y_test, y_pred_gdb))

con_matrix = []
con_matrix = confusion_matrix(y_test, y_pred_gdb)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("GradientBoosting accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("GradientBoosting accuracy of precision false: ",P_false)

GradientBoosting accuracy:  0.630372492837
[[ 80 214]
 [ 44 360]]
GradientBoosting accuracy of precision true:  0.645161290323
GradientBoosting accuracy of precision false:  0.627177700348


# Use Cross Validation Data, Train: Test = 1:9

In [14]:
# running linear SVM model
clf_svm = LinearSVC()
clf_svm.fit(X_test, y_test)
y_pred_svm = clf_svm.predict(X_train)
acc_svm = accuracy_score(y_train, y_pred_svm)
print ("Linear SVM accuracy: ",acc_svm)
print (confusion_matrix(y_train, y_pred_svm))

con_matrix = []
con_matrix = confusion_matrix(y_train, y_pred_svm)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("Linear SVM accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("Linear SVM accuracy of precision false: ",P_false)

Linear SVM accuracy:  0.601307189542
[[ 202 2317]
 [ 184 3570]]
Linear SVM accuracy of precision true:  0.523316062176
Linear SVM accuracy of precision false:  0.606420927467


In [15]:
# running random forest model
clf_rf = RandomForestClassifier()
clf_rf.fit(X_test, y_test)
y_pred_rf = clf_rf.predict(X_train)
acc_rf = accuracy_score(y_train, y_pred_rf)
print ("random forest accuracy: ",acc_rf)
print (confusion_matrix(y_train, y_pred_rf))

con_matrix = []
con_matrix = confusion_matrix(y_train, y_pred_rf)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("random forest accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("random forest accuracy of precision false: ",P_false)

random forest accuracy:  0.561294436474
[[1129 1390]
 [1362 2392]]
random forest accuracy of precision true:  0.453231633882
random forest accuracy of precision false:  0.632469592808


In [16]:
# running Stochastic Gradient Descent model
clf_sgd = SGDClassifier()
clf_sgd.fit(X_test, y_test)
y_pred_sgd = clf_sgd.predict(X_train)
acc_sgd = accuracy_score(y_train, y_pred_sgd)
print ("stochastic gradient descent accuracy: ",acc_sgd)
print (confusion_matrix(y_train, y_pred_sgd))

con_matrix = []
con_matrix = confusion_matrix(y_train, y_pred_sgd)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("stochastic gradient descent accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("stochastic gradient descent accuracy of precision false: ",P_false)

stochastic gradient descent accuracy:  0.598437749083
[[   0 2519]
 [   0 3754]]
stochastic gradient descent accuracy of precision true:  nan
stochastic gradient descent accuracy of precision false:  0.598437749083


/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/ipykernel_launcher.py:11: RuntimeWarning: invalid value encountered in long_scalars
  # This is added back by InteractiveShellApp.init_path()


In [17]:
# running Nearest Neighbors model
clf_knn = KNeighborsClassifier()
clf_knn.fit(X_test, y_test)
y_pred_knn = clf_knn.predict(X_train)
acc_knn = accuracy_score(y_train, y_pred_knn)
print ("nearest neighbors accuracy: ",acc_knn)
print (confusion_matrix(y_train, y_pred_knn))

con_matrix = []
con_matrix = confusion_matrix(y_train, y_pred_knn)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("k nearest neighbors accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("k nearest neighbors accuracy of precision false: ",P_false)

nearest neighbors accuracy:  0.605930176949
[[1103 1416]
 [1056 2698]]
k nearest neighbors accuracy of precision true:  0.510884668828
k nearest neighbors accuracy of precision false:  0.655809431211


In [18]:
# running AdaBoostClassifier model
clf_ada = AdaBoostClassifier()
clf_ada.fit(X_test, y_test)
y_pred_ada = clf_ada.predict(X_train)
acc_ada = accuracy_score(y_train, y_pred_ada)
print ("AdaBoost accuracy: ",acc_ada)
print (confusion_matrix(y_train, y_pred_ada))

con_matrix = []
con_matrix = confusion_matrix(y_train, y_pred_ada)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("AdaBoost accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("AdaBoost accuracy of precision false: ",P_false)

AdaBoost accuracy:  0.563526223498
[[ 921 1598]
 [1140 2614]]
AdaBoost accuracy of precision true:  0.446870451237
AdaBoost accuracy of precision false:  0.620607787274


In [19]:
# running GradientBoosting model
clf_gdb = GradientBoostingClassifier()
clf_gdb.fit(X_test, y_test)
y_pred_gdb = clf_gdb.predict(X_train)
acc_gdb = accuracy_score(y_train, y_pred_gdb)
print ("GradientBoosting accuracy: ",acc_gdb)
print (confusion_matrix(y_train, y_pred_gdb))

con_matrix = []
con_matrix = confusion_matrix(y_train, y_pred_gdb)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("GradientBoosting accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("GradientBoosting accuracy of precision false: ",P_false)

GradientBoosting accuracy:  0.582655826558
[[ 753 1766]
 [ 852 2902]]
GradientBoosting accuracy of precision true:  0.469158878505
GradientBoosting accuracy of precision false:  0.621679520137


In [20]:
# We'd like to integrate cross validation with another idea: grid search.
# Grid search allows us to create models with different hyperparameters and test them all.
# It also allows us to determine the best hyperparameter values.
from sklearn.model_selection import GridSearchCV
from sklearn.svm import SVC

parameters = {'kernel':('linear', 'rbf'), 'C':[0.001, 0.01, 0.1, 1, 10]}
svc = SVC(random_state=100)
clf = GridSearchCV(svc, parameters, cv=5)
clf.fit(X, y)
print('Best score', clf.best_score_)
print(clf.best_estimator_)

Best score 0.596471094535
SVC(C=0.001, cache_size=200, class_weight=None, coef0=0.0,
  decision_function_shape='ovr', degree=3, gamma='auto', kernel='linear',
  max_iter=-1, probability=False, random_state=100, shrinking=True,
  tol=0.001, verbose=False)


# Shuffled Cross Validation Data, Train : Test = 9:1

In [21]:
from sklearn.utils import shuffle
shffule_traing_df = shuffle(traing_df)

shffule_X = shffule_traing_df[features]
shffule_y = shffule_traing_df['Label']
shffule_X_train, shffule_X_test, shffule_y_train, shffule_y_test = cross_validation.train_test_split(shffule_X/10.,shffule_y,test_size=0.1,random_state=0)

In [22]:
# running SVM model
clf_svm = LinearSVC()
clf_svm.fit(shffule_X_train, shffule_y_train)
shffule_y_pred_svm = clf_svm.predict(shffule_X_test)
shffule_acc_svm = accuracy_score(shffule_y_test, shffule_y_pred_svm)
print ("Shffuled Linear SVM accuracy: ",shffule_acc_svm)
print (confusion_matrix(shffule_y_test, shffule_y_pred_svm))

con_matrix = []
con_matrix = confusion_matrix(shffule_y_test, shffule_y_pred_svm)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("Shffuled Linear SVM accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("Shffuled Linear SVM accuracy of precision false: ",P_false)

Shffuled Linear SVM accuracy:  0.593123209169
[[  4 279]
 [  5 410]]
Shffuled Linear SVM accuracy of precision true:  0.444444444444
Shffuled Linear SVM accuracy of precision false:  0.595065312046


In [23]:
# running random forest model
clf_rf = RandomForestClassifier()
clf_rf.fit(shffule_X_train, shffule_y_train)
shffule_y_pred_rf = clf_rf.predict(shffule_X_test)
shffule_acc_rf = accuracy_score(shffule_y_test, shffule_y_pred_rf)
print ("Shffuled random forest accuracy: ",shffule_acc_rf)
print (confusion_matrix(shffule_y_test, shffule_y_pred_rf))

con_matrix = []
con_matrix = confusion_matrix(shffule_y_test, shffule_y_pred_rf)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("Shffuled random forest accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("Shffuled random forest accuracy of precision false: ",P_false)

Shffuled random forest accuracy:  0.651862464183
[[168 115]
 [128 287]]
Shffuled random forest accuracy of precision true:  0.567567567568
Shffuled random forest accuracy of precision false:  0.713930348259


In [55]:
# running AdaBoostClassifier model
clf_ada = AdaBoostClassifier()
clf_ada.fit(shffule_X_train, shffule_y_train)
shffule_y_pred_ada = clf_ada.predict(shffule_X_test)
shffule_acc_ada = accuracy_score(shffule_y_test, shffule_y_pred_ada)
print ("Shffuled AdaBoost accuracy: ",shffule_acc_ada)
print (confusion_matrix(shffule_y_test, shffule_y_pred_ada))

con_matrix = []
con_matrix = confusion_matrix(shffule_y_test, shffule_y_pred_ada)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("Shffuled AdaBoost accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("Shffuled AdaBoost accuracy of precision false: ",P_false)

Shffuled AdaBoost accuracy:  0.597421203438
[[ 53 230]
 [ 51 364]]
Shffuled AdaBoost accuracy of precision true:  0.509615384615
Shffuled AdaBoost accuracy of precision false:  0.612794612795


In [25]:
# running Stochastic Gradient Descent model
clf_sgd = SGDClassifier()
clf_sgd.fit(shffule_X_train, shffule_y_train)
shffule_y_pred_sgd = clf_sgd.predict(shffule_X_test)
shffule_acc_sgd = accuracy_score(shffule_y_test, shffule_y_pred_sgd)
print ("Shffuled stochastic gradient descent accuracy: ",shffule_acc_sgd)
print (confusion_matrix(shffule_y_test, shffule_y_pred_sgd))

con_matrix = []
con_matrix = confusion_matrix(shffule_y_test, shffule_y_pred_sgd)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("Shffuled stochastic gradient descent accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("Shffuled stochastic gradient descent accuracy of precision false: ",P_false)

Shffuled stochastic gradient descent accuracy:  0.406876790831
[[283   0]
 [414   1]]
Shffuled stochastic gradient descent accuracy of precision true:  0.406025824964
Shffuled stochastic gradient descent accuracy of precision false:  1.0


/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)


In [26]:
# running Nearest Neighbors model
clf_knn = KNeighborsClassifier()
clf_knn.fit(shffule_X_train, shffule_y_train)
shffule_y_pred_knn = clf_knn.predict(shffule_X_test)
shffule_acc_knn = accuracy_score(shffule_y_test, shffule_y_pred_knn)
print ("Shffuled nearest neighbors accuracy: ",shffule_acc_knn)
print (confusion_matrix(shffule_y_test, shffule_y_pred_knn))

con_matrix = []
con_matrix = confusion_matrix(shffule_y_test, shffule_y_pred_knn)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("Shffuled nearest neighbors accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("Shffuled nearest neighbors accuracy of precision false: ",P_false)

Shffuled nearest neighbors accuracy:  0.830945558739
[[217  66]
 [ 52 363]]
Shffuled nearest neighbors accuracy of precision true:  0.806691449814
Shffuled nearest neighbors accuracy of precision false:  0.846153846154


In [47]:
# running GradientBoosting model
clf_gdb = GradientBoostingClassifier()
clf_gdb.fit(shffule_X_train, shffule_y_train)
shffule_y_pred_gdb = clf_gdb.predict(X_test)
shffule_acc_gdb = accuracy_score(shffule_y_test, shffule_y_pred_gdb)
print ("GradientBoosting accuracy: ",shffule_acc_gdb)
print (confusion_matrix(shffule_y_test, shffule_y_pred_gdb))

con_matrix = []
con_matrix = confusion_matrix(shffule_y_test, shffule_y_pred_gdb)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("Shuffled GradientBoosting accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("Shffuled GradientBoosting accuracy of precision false: ",P_false)

GradientBoosting accuracy:  0.541547277937
[[ 46 237]
 [ 83 332]]
Shuffled GradientBoosting accuracy of precision true:  0.356589147287
Shffuled GradientBoosting accuracy of precision false:  0.583479789104


# Use Shuffled Cross Validation Data, Train:Test = 1:9

In [27]:
# running SVM model
clf_svm = LinearSVC()
clf_svm.fit(shffule_X_test, shffule_y_test)
shffule_y_pred_svm = clf_svm.predict(shffule_X_train)
shffule_acc_svm = accuracy_score(shffule_y_train, shffule_y_pred_svm)
print ("Shffuled Linear SVM accuracy: ",shffule_acc_svm)
print (confusion_matrix(shffule_y_train, shffule_y_pred_svm))

con_matrix = []
con_matrix = confusion_matrix(shffule_y_train, shffule_y_pred_svm)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("Shffuled Linear SVM accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("Shffuled Linear SVM accuracy of precision false: ",P_false)

Shffuled Linear SVM accuracy:  0.596843615495
[[  24 2506]
 [  23 3720]]
Shffuled Linear SVM accuracy of precision true:  0.510638297872
Shffuled Linear SVM accuracy of precision false:  0.597494378413


In [52]:
# running random forest model
clf_rf = RandomForestClassifier()
clf_rf.fit(shffule_X_test, shffule_y_test)
shffule_y_pred_rf = clf_rf.predict(shffule_X_train)
shffule_acc_rf = accuracy_score(shffule_y_train, shffule_y_pred_rf)
print ("Shffuled random forest accuracy: ",shffule_acc_rf)
print (confusion_matrix(shffule_y_train, shffule_y_pred_rf))

con_matrix = []
con_matrix = confusion_matrix(shffule_y_train, shffule_y_pred_rf)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("Shffuled random forest accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("Shffuled random forest accuracy of precision false: ",P_false)

Shffuled random forest accuracy:  0.541048939901
[[1122 1408]
 [1471 2272]]
Shffuled random forest accuracy of precision true:  0.432703432318
Shffuled random forest accuracy of precision false:  0.617391304348


In [53]:
# running AdaBoostClassifier model
clf_ada = AdaBoostClassifier()
clf_ada.fit(shffule_X_test, shffule_y_test)
shffule_y_pred_ada = clf_ada.predict(shffule_X_train)
shffule_acc_ada = accuracy_score(shffule_y_train, shffule_y_pred_ada)
print ("Shffuled AdaBoost accuracy: ",shffule_acc_ada)
print (confusion_matrix(shffule_y_train, shffule_y_pred_ada))

con_matrix = []
con_matrix = confusion_matrix(shffule_y_train, shffule_y_pred_ada)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("Shffuled AdaBoost accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("Shffuled AdaBoost accuracy of precision false: ",P_false)

Shffuled AdaBoost accuracy:  0.55220787502
[[ 905 1625]
 [1184 2559]]
Shffuled AdaBoost accuracy of precision true:  0.433221637147
Shffuled AdaBoost accuracy of precision false:  0.611615678776


In [30]:
# running Stochastic Gradient Descent model
clf_sgd = SGDClassifier()
clf_sgd.fit(shffule_X_test, shffule_y_test)
shffule_y_pred_sgd = clf_sgd.predict(shffule_X_train)
shffule_acc_sgd = accuracy_score(shffule_y_train, shffule_y_pred_sgd)
print ("Shffuled stochastic gradient descent accuracy: ",shffule_acc_sgd)
print (confusion_matrix(shffule_y_train, shffule_y_pred_sgd))

con_matrix = []
con_matrix = confusion_matrix(shffule_y_train, shffule_y_pred_sgd)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("Shffuled stochastic gradient descent accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("Shffuled stochastic gradient descent accuracy of precision false: ",P_false)

Shffuled stochastic gradient descent accuracy:  0.403315797864
[[2530    0]
 [3743    0]]
Shffuled stochastic gradient descent accuracy of precision true:  0.403315797864
Shffuled stochastic gradient descent accuracy of precision false:  nan


/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/ipykernel_launcher.py:13: RuntimeWarning: invalid value encountered in long_scalars
  del sys.path[0]


In [31]:
# running Nearest Neighbors model
clf_knn = KNeighborsClassifier()
clf_knn.fit(shffule_X_test, shffule_y_test)
shffule_y_pred_knn = clf_knn.predict(shffule_X_train)
shffule_acc_knn = accuracy_score(shffule_y_train, shffule_y_pred_knn)
print ("Shffuled nearest neighbors accuracy: ",shffule_acc_knn)
print (confusion_matrix(shffule_y_train, shffule_y_pred_knn))

con_matrix = []
con_matrix = confusion_matrix(shffule_y_train, shffule_y_pred_knn)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("Shffuled nearest neighbors accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("Shffuled nearest neighbors accuracy of precision false: ",P_false)

Shffuled nearest neighbors accuracy:  0.591423561294
[[1018 1512]
 [1051 2692]]
Shffuled nearest neighbors accuracy of precision true:  0.492025132914
Shffuled nearest neighbors accuracy of precision false:  0.640342530923


In [45]:
# running GradientBoosting model
clf_gdb = GradientBoostingClassifier()
clf_gdb.fit(shffule_X_test, shffule_y_test)
shffule_y_pred_gdb = clf_gdb.predict(shffule_X_train)
shffule_acc_gdb = accuracy_score(shffule_y_train, shffule_y_pred_gdb)
print ("GradientBoosting accuracy: ",shffule_acc_gdb)
print (confusion_matrix(shffule_y_train, shffule_y_pred_gdb))

con_matrix = []
con_matrix = confusion_matrix(shffule_y_train, shffule_y_pred_gdb)
P_true = con_matrix[0][0] / (con_matrix[0][0] + con_matrix[1][0])
print ("ShuffledGradientBoosting accuracy of precision true: ",P_true)
P_false = con_matrix[1][1] / (con_matrix[0][1] + con_matrix[1][1])
print ("Shuffled GradientBoosting accuracy of precision false: ",P_false)

GradientBoosting accuracy:  0.580742866252
[[ 765 1765]
 [ 865 2878]]
ShuffledGradientBoosting accuracy of precision true:  0.469325153374
Shuffled GradientBoosting accuracy of precision false:  0.619857850528
